In [1]:
import opentnsim
print('This notebook has been tested with OpenTNSim version {} - branch: Afstuderen_LoesSegers'.format(opentnsim.__version__))



This notebook has been tested with OpenTNSim version 1.0.0 - branch: Afstuderen_LoesSegers


In [2]:
# package(s) related to time, space and id
import datetime, time
import platform
import random
import os
import pathlib
import io
import urllib
import tempfile
import functools
import logging
import pickle

# package(s) related to the simulation
import simpy
from simpy.util import start_delayed
import networkx as nx  

# OpenTNSIM
import opentnsim.core as core
import opentnsim.graph_module as graph_module
import opentnsim.plot as plot
import opentnsim.model as model

# spatial libraries 
import shapely.geometry
import shapely.wkt
import pyproj
import shapely.geometry
from osgeo import ogr, osr
from simplekml import Kml, Style
import folium

# package(s) for data handling
import requests
import math             
import json
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
%matplotlib inline

logging.basicConfig(level=logging.INFO)
logger = logging.getLogger()

# define the coorinate system
geod = pyproj.Geod(ellps="WGS84")

## Load the network graphs from pickle files

In [3]:
#Load graph
with open("graph0.pickle", 'rb') as f:  # notice the r instead of w
    FG_t0 = pickle.load(f)

In [4]:
FG_t0 = FG_t0

In [5]:
#Load graph
with open("graph1.pickle", 'rb') as f:  # notice the r instead of w
    FG_sl = pickle.load(f)

In [6]:
FG_sl = FG_sl

### Check t0 emission scenario

In [7]:
#The CO2 emissions are plotted

p = folium.Map(location=[51.55, 4.30], zoom_start = 10,  tiles="cartodbpositron")

for edge in FG_t0.edges(data = True):
    points_x = list(edge[2]["Info"]["geometry"].coords.xy[0])
    points_y = list(edge[2]["Info"]["geometry"].coords.xy[1])
    
    line = []
    for i, _ in enumerate(points_x):
        line.append((points_y[i], points_x[i]))
        
    if 0 < edge[2]["Info"]["WidePushedWidth"] <= 200:
        folium.PolyLine(line, color = "moccasin", weight = 2, popup = edge[2]["Info"]["WidePushedWidth"]).add_to(p)
        
    elif 200 < edge[2]["Info"]["WidePushedWidth"] <= 500:
        folium.PolyLine(line, color = "yellow", weight = 3, popup = edge[2]["Info"]["WidePushedWidth"]).add_to(p)
        
    elif 500 < edge[2]["Info"]["WidePushedWidth"] <= 1000:
        folium.PolyLine(line, color = "gold", weight = 3, popup = edge[2]["Info"]["WidePushedWidth"]).add_to(p)
    
    elif 1000 < edge[2]["Info"]["WidePushedWidth"] <= 2000:
        folium.PolyLine(line, color = "goldenrod", weight = 3, popup = edge[2]["Info"]["WidePushedWidth"]).add_to(p)
    
    elif 2000 < edge[2]["Info"]["WidePushedWidth"] <= 3000:
        folium.PolyLine(line, color = "orange", weight = 3, popup = edge[2]["Info"]["WidePushedWidth"]).add_to(p)
        
    elif 3000 < edge[2]["Info"]["WidePushedWidth"] <= 4000:
        folium.PolyLine(line, color = "orangered", weight = 3, popup = edge[2]["Info"]["WidePushedWidth"]).add_to(p)
        
    elif 4000 < edge[2]["Info"]["WidePushedWidth"] <= 5000:
        folium.PolyLine(line, color = "red", weight = 3, popup = edge[2]["Info"]["WidePushedWidth"]).add_to(p)
    
    elif edge[2]["Info"]["WidePushedWidth"] > 5000:
        folium.PolyLine(line, color = "darkred", weight = 5, popup = edge[2]["Info"]["WidePushedWidth"]).add_to(p)
        
    else:
        folium.PolyLine(line, color = 'lightgrey', weight = 1, popup = edge[2]["Info"]["WidePushedWidth"]).add_to(p)
        

p

### Check speed limit scenario

In [8]:
#The CO2 emissions are plotted

p = folium.Map(location=[51.55, 4.30], zoom_start = 10,  tiles="cartodbpositron")

for edge in FG_sl.edges(data = True):
    points_x = list(edge[2]["Info"]["geometry"].coords.xy[0])
    points_y = list(edge[2]["Info"]["geometry"].coords.xy[1])
    
    line = []
    for i, _ in enumerate(points_x):
        line.append((points_y[i], points_x[i]))
        
    if 0 < edge[2]["Info"]["WidePushedWidth"] <= 200:
        folium.PolyLine(line, color = "moccasin", weight = 2, popup = edge[2]["Info"]["WidePushedWidth"]).add_to(p)
        
    elif 200 < edge[2]["Info"]["WidePushedWidth"] <= 500:
        folium.PolyLine(line, color = "yellow", weight = 3, popup = edge[2]["Info"]["WidePushedWidth"]).add_to(p)
        
    elif 500 < edge[2]["Info"]["WidePushedWidth"] <= 1000:
        folium.PolyLine(line, color = "gold", weight = 3, popup = edge[2]["Info"]["WidePushedWidth"]).add_to(p)
    
    elif 1000 < edge[2]["Info"]["WidePushedWidth"] <= 2000:
        folium.PolyLine(line, color = "goldenrod", weight = 3, popup = edge[2]["Info"]["WidePushedWidth"]).add_to(p)
    
    elif 2000 < edge[2]["Info"]["WidePushedWidth"] <= 3000:
        folium.PolyLine(line, color = "orange", weight = 3, popup = edge[2]["Info"]["WidePushedWidth"]).add_to(p)
        
    elif 3000 < edge[2]["Info"]["WidePushedWidth"] <= 4000:
        folium.PolyLine(line, color = "orangered", weight = 3, popup = edge[2]["Info"]["WidePushedWidth"]).add_to(p)
        
    elif 4000 < edge[2]["Info"]["WidePushedWidth"] <= 5000:
        folium.PolyLine(line, color = "red", weight = 3, popup = edge[2]["Info"]["WidePushedWidth"]).add_to(p)
    
    elif edge[2]["Info"]["WidePushedWidth"] > 5000:
        folium.PolyLine(line, color = "darkred", weight = 5, popup = edge[2]["Info"]["WidePushedWidth"]).add_to(p)
        
    else:
        folium.PolyLine(line, color = 'lightgrey', weight = 1, popup = edge[2]["Info"]["WidePushedWidth"]).add_to(p)
        

p

### Make lists that contain all the information you need for a difference map

In [9]:
list_node_start = []
list_node_stop = []
list_CO2 = []
list_PM10 = []
list_NOX = []


for edge in FG_t0.edges(data = True):
    if edge[2]["Info"]["WidePushedWidth"] > 0:
        list_node_start.append(edge[2]["Info"]["StartJunctionId"])
        list_node_stop.append(edge[2]["Info"]["EndJunctionId"])
        list_CO2.append(edge[2]["Info"]["WidePushedWidth"])
        list_PM10.append(edge[2]["Info"]["WidePushedLength"])
        list_NOX.append(edge[2]["Info"]["WidePushedDepth"])

In [10]:
list_CO2_1 = []
list_PM10_1 = []
list_NOX_1 = []


for edge in FG_sl.edges(data = True):
    if edge[2]["Info"]["WidePushedWidth"] > 0:
        list_CO2_1.append(edge[2]["Info"]["WidePushedWidth"])
        list_PM10_1.append(edge[2]["Info"]["WidePushedLength"])
        list_NOX_1.append(edge[2]["Info"]["WidePushedDepth"])

In [48]:
# We can shorten the above cells to this:
df_t0 = nx.to_pandas_edgelist(FG_t0)
df_sl = nx.to_pandas_edgelist(FG_sl)

for df_i in [df_t0, df_sl]:
    # What is going on here..... 
    # CO2, PM10, NOX  stored in the variable WidePushedWidth/Length/Depth... why?
    df_i['CO2'] = df_i["Info"].apply(lambda x: x["WidePushedWidth"])
    df_i['PM10'] = df_i["Info"].apply(lambda x: x["WidePushedLength"])
    df_i['NOX'] = df_i["Info"].apply(lambda x: x["WidePushedDepth"])

# select rows
df_t0 = df_t0[df_t0['CO2'] > 0]
df_sl = df_sl[df_sl['CO2'] > 0]


### Create a dataframe

In [ ]:
# We can now shorten this to:
df = pd.merge(
    df_t0, 
    df_sl, 
    suffixes=('_t0', '_sl'), 
    left_on=['source', 'target'], 
    right_on=['source', 'target']
)


In [52]:
# TODO: this does not work because the number of nodes are not equal
# df['node_start'] = list_node_start
# df['node_stop'] = list_node_stop
# df['CO2_t0'] = list_CO2
# df['CO2_sl'] = list_CO2_1
# df['PM10_t0'] = list_PM10
# df['PM10_sl'] = list_PM10_1
# df['NOX_t0'] = list_NOX
# df['NOX_sl'] = list_NOX_1

### Compute absolute difference between two scenarios

In [61]:

df['CO2_diff'] = np.abs(df['CO2_sl'] - df['CO2_t0'])
df['PM10_diff'] = np.abs(df['PM10_sl'] - df['PM10_t0'])
df['NOX_diff'] = np.abs(df['NOX_sl'] - df['NOX_t0'])

### Create a new graph (FG_diff) and add absolute emission difference per edge on the network

In [63]:
FG_diff = FG_t0.copy()

In [64]:
#We loop through all edges: in case the StartJunctionId and EndJunctionId are equal to the node names of the
#Start and stop point of the edges of the dataframe, then the emission is assigned to that edge

#It works as a summation

for i in range(len(list_node_start)):
    
    for edge in FG_diff.edges(data = True):
        
        if edge[2]["Info"]["StartJunctionId"] == list_node_start[i] and edge[2]["Info"]["EndJunctionId"] == list_node_stop[i]:
            edge[2]["Info"]["WidePushedWidth"] = df['CO2_diff'].iloc[i]
            edge[2]["Info"]["WidePushedLength"] = df['PM10_diff'].iloc[i]
            edge[2]["Info"]["WidePushedDepth"] = df['NOX_diff'].iloc[i]

IndexError: single positional indexer is out-of-bounds

### CO2 emission differences

In [ ]:
#The CO2 emissions are plotted

p = folium.Map(location=[51.55, 4.30], zoom_start = 10,  tiles="cartodbpositron")

for edge in FG_diff.edges(data = True):
    points_x = list(edge[2]["Info"]["geometry"].coords.xy[0])
    points_y = list(edge[2]["Info"]["geometry"].coords.xy[1])
    
    line = []
    for i, _ in enumerate(points_x):
        line.append((points_y[i], points_x[i]))
        
    if 0 < edge[2]["Info"]["WidePushedWidth"] <= 100:
        folium.PolyLine(line, color = "moccasin", weight = 2, popup = edge[2]["Info"]["WidePushedWidth"]).add_to(p)
        
    elif 100 < edge[2]["Info"]["WidePushedWidth"] <= 200:
        folium.PolyLine(line, color = "yellow", weight = 3, popup = edge[2]["Info"]["WidePushedWidth"]).add_to(p)
        
    elif 200 < edge[2]["Info"]["WidePushedWidth"] <= 300:
        folium.PolyLine(line, color = "gold", weight = 3, popup = edge[2]["Info"]["WidePushedWidth"]).add_to(p)
    
    elif 300 < edge[2]["Info"]["WidePushedWidth"] <= 400:
        folium.PolyLine(line, color = "goldenrod", weight = 3, popup = edge[2]["Info"]["WidePushedWidth"]).add_to(p)
    
    elif 400 < edge[2]["Info"]["WidePushedWidth"] <= 500:
        folium.PolyLine(line, color = "orange", weight = 3, popup = edge[2]["Info"]["WidePushedWidth"]).add_to(p)
        
    elif 500 < edge[2]["Info"]["WidePushedWidth"] <= 750:
        folium.PolyLine(line, color = "orangered", weight = 3, popup = edge[2]["Info"]["WidePushedWidth"]).add_to(p)
        
    elif 750 < edge[2]["Info"]["WidePushedWidth"] <= 1000:
        folium.PolyLine(line, color = "red", weight = 3, popup = edge[2]["Info"]["WidePushedWidth"]).add_to(p)
    
    elif edge[2]["Info"]["WidePushedWidth"] > 1000:
        folium.PolyLine(line, color = "darkred", weight = 5, popup = edge[2]["Info"]["WidePushedWidth"]).add_to(p)
        
    else:
        folium.PolyLine(line, color = 'lightgrey', weight = 1, popup = edge[2]["Info"]["WidePushedWidth"]).add_to(p)
        

p

In [ ]:
#The PM10 emissions are plotted

q = folium.Map(location=[51.55, 4.30], zoom_start = 10,  tiles="cartodbpositron")

for edge in FG_diff.edges(data = True):
    points_x = list(edge[2]["Info"]["geometry"].coords.xy[0])
    points_y = list(edge[2]["Info"]["geometry"].coords.xy[1])
    
    line = []
    for i, _ in enumerate(points_x):
        line.append((points_y[i], points_x[i]))
        
    
    if 0 < edge[2]["Info"]["WidePushedLength"] <= 0.025:
        folium.PolyLine(line, color = "azure", weight = 2, popup = edge[2]["Info"]["WidePushedLength"]).add_to(q)
        
    elif 0.025 < edge[2]["Info"]["WidePushedLength"] <= 0.05:
        folium.PolyLine(line, color = "lightskyblue", weight = 3, popup = edge[2]["Info"]["WidePushedLength"]).add_to(q)
        
    elif 0.05 < edge[2]["Info"]["WidePushedLength"] <= 0.1:
        folium.PolyLine(line, color = "mediumturquoise", weight = 3, popup = edge[2]["Info"]["WidePushedLength"]).add_to(q)
    
    elif 0.1 < edge[2]["Info"]["WidePushedLength"] <= 0.2:
        folium.PolyLine(line, color = "lightseagreen", weight = 3, popup = edge[2]["Info"]["WidePushedLength"]).add_to(q)
    
    elif 0.2 < edge[2]["Info"]["WidePushedLength"] <= 0.4:
        folium.PolyLine(line, color = "mediumseagreen", weight = 3, popup = edge[2]["Info"]["WidePushedLength"]).add_to(q)
        
    elif 0.4 < edge[2]["Info"]["WidePushedLength"] <= 0.6:
        folium.PolyLine(line, color = "teal", weight = 3, popup = edge[2]["Info"]["WidePushedLength"]).add_to(q)
        
    elif 0.6 < edge[2]["Info"]["WidePushedLength"] <= 0.8:
        folium.PolyLine(line, color = "green", weight = 3, popup = edge[2]["Info"]["WidePushedLength"]).add_to(q)
    
    elif edge[2]["Info"]["WidePushedLength"] > 0.8:
        folium.PolyLine(line, color = "darkslategrey", weight =5, popup = edge[2]["Info"]["WidePushedLength"]).add_to(q)
        
    else:
        folium.PolyLine(line, color = 'lightgrey', weight = 1, popup = edge[2]["Info"]["WidePushedLength"]).add_to(q)
        

q

In [ ]:
#The PM10 emissions are plotted

r = folium.Map(location=[51.55, 4.30], zoom_start = 10,  tiles="cartodbpositron")

for edge in FG_diff.edges(data = True):
    points_x = list(edge[2]["Info"]["geometry"].coords.xy[0])
    points_y = list(edge[2]["Info"]["geometry"].coords.xy[1])
    
    line = []
    for i, _ in enumerate(points_x):
        line.append((points_y[i], points_x[i]))
        
    
    if 0 < edge[2]["Info"]["WidePushedDepth"] <= 1:
        folium.PolyLine(line, color = "lavenderblush", weight = 2, popup = edge[2]["Info"]["WidePushedDepth"]).add_to(r)
        
    elif 1 < edge[2]["Info"]["WidePushedDepth"] <= 2:
        folium.PolyLine(line, color = "pink", weight = 3, popup = edge[2]["Info"]["WidePushedDepth"]).add_to(r)
        
    elif 2 < edge[2]["Info"]["WidePushedDepth"] <= 3:
        folium.PolyLine(line, color = "hotpink", weight = 3, popup = edge[2]["Info"]["WidePushedDepth"]).add_to(r)
    
    elif 3 < edge[2]["Info"]["WidePushedDepth"] <= 4:
        folium.PolyLine(line, color = "plum", weight = 3, popup = edge[2]["Info"]["WidePushedDepth"]).add_to(r)
    
    elif 4 < edge[2]["Info"]["WidePushedDepth"] <= 5:
        folium.PolyLine(line, color = "orchid", weight = 3, popup = edge[2]["Info"]["WidePushedDepth"]).add_to(r)
        
    elif 5 < edge[2]["Info"]["WidePushedDepth"] <= 7.50:
        folium.PolyLine(line, color = "mediumorchid", weight = 3, popup = edge[2]["Info"]["WidePushedDepth"]).add_to(r)
        
    elif 7.50 < edge[2]["Info"]["WidePushedDepth"] <= 10:
        folium.PolyLine(line, color = "darkviolet", weight = 3, popup = edge[2]["Info"]["WidePushedDepth"]).add_to(r)
    
    elif edge[2]["Info"]["WidePushedDepth"] > 10:
        folium.PolyLine(line, color = "rebeccapurple", weight = 5, popup = edge[2]["Info"]["WidePushedDepth"]).add_to(r)
        
    else:
        folium.PolyLine(line, color = 'lightgrey', weight = 1, popup = edge[2]["Info"]["WidePushedDepth"]).add_to(r)
        

r